# Diplodatos Kaggle Competition

We present this peace of code to create the baseline for the competition, and as an example of how to deal with these kind of problems. The main goals are that you:

1. Explore the data and learn from it
1. Try different models and see which one fits the best the given data
1. Get a higher score than the given one in the current baseline example
1. Try to get the highest score in the class :)

In [1]:
# Import the required packages
import os

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pandas_profiling import ProfileReport
from sklearn.metrics import confusion_matrix
from sklearn.metrics import f1_score
from sklearn.metrics import classification_report
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import KBinsDiscretizer
from sklearn.tree import DecisionTreeClassifier
from sklearn.base import clone

## Read Data

In [2]:
train_df = pd.read_csv("../data/travel_insurance_prediction_train.csv")
test_df = pd.read_csv("../data/travel_insurance_prediction_test.csv")

## Explore the Data

Is your task to explore the data, do analysis over it and get insights, then use those insights to better pick a model.

In [3]:
train_df.head()

Customer  Age               Employment Type GraduateOrNot  AnnualIncome  \
0         1   33  Private Sector/Self Employed           Yes        550000   
1         2   28  Private Sector/Self Employed           Yes        800000   
2         3   31  Private Sector/Self Employed           Yes       1250000   
3         4   31             Government Sector            No        300000   
4         5   28  Private Sector/Self Employed           Yes       1250000   

   FamilyMembers  ChronicDiseases FrequentFlyer EverTravelledAbroad  \
0              6                0            No                  No   
1              7                0           Yes                  No   
2              4                0            No                  No   
3              7                0            No                  No   
4              3                0            No                  No   

   TravelInsurance  
0                1  
1                0  
2                0  
3                0  
4                0

In [8]:
print(round(sum(train_df['TravelInsurance'])/len(train_df)*100, 2), '% de los datos pertenece a la clase positiva, o sea, el dataset está levemente desbalanceado')

35.7 % de los datos pertenece a la clase positiva, o sea, el dataset está levemente desbalanceado


In [9]:
test_df.head()

Customer  Age               Employment Type GraduateOrNot  AnnualIncome  \
0      1491   29  Private Sector/Self Employed           Yes       1100000   
1      1492   28  Private Sector/Self Employed           Yes        750000   
2      1493   31             Government Sector           Yes       1500000   
3      1494   28  Private Sector/Self Employed           Yes       1400000   
4      1495   33  Private Sector/Self Employed           Yes       1500000   

   FamilyMembers  ChronicDiseases FrequentFlyer EverTravelledAbroad  
0              4                0            No                  No  
1              5                1           Yes                  No  
2              4                0           Yes                 Yes  
3              3                0            No                 Yes  
4              4                0           Yes                 Yes

**TravelInsurance** is the column that we should predict. That column is not present in the test set.

In [10]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1490 entries, 0 to 1489
Data columns (total 10 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   Customer             1490 non-null   int64 
 1   Age                  1490 non-null   int64 
 2   Employment Type      1490 non-null   object
 3   GraduateOrNot        1490 non-null   object
 4   AnnualIncome         1490 non-null   int64 
 5   FamilyMembers        1490 non-null   int64 
 6   ChronicDiseases      1490 non-null   int64 
 7   FrequentFlyer        1490 non-null   object
 8   EverTravelledAbroad  1490 non-null   object
 9   TravelInsurance      1490 non-null   int64 
dtypes: int64(6), object(4)
memory usage: 116.5+ KB


In [11]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 497 entries, 0 to 496
Data columns (total 9 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   Customer             497 non-null    int64 
 1   Age                  497 non-null    int64 
 2   Employment Type      497 non-null    object
 3   GraduateOrNot        497 non-null    object
 4   AnnualIncome         497 non-null    int64 
 5   FamilyMembers        497 non-null    int64 
 6   ChronicDiseases      497 non-null    int64 
 7   FrequentFlyer        497 non-null    object
 8   EverTravelledAbroad  497 non-null    object
dtypes: int64(5), object(4)
memory usage: 35.1+ KB


No hay valores faltantes

In [12]:
train_df.describe().round(3)

Customer       Age  AnnualIncome  FamilyMembers  ChronicDiseases  \
count   1490.00  1490.000      1490.000       1490.000         1490.000   
mean     745.50    29.667    927818.792          4.777            0.276   
std      430.27     2.881    381171.545          1.640            0.447   
min        1.00    25.000    300000.000          2.000            0.000   
25%      373.25    28.000    600000.000          4.000            0.000   
50%      745.50    29.000    900000.000          5.000            0.000   
75%     1117.75    32.000   1250000.000          6.000            1.000   
max     1490.00    35.000   1800000.000          9.000            1.000   

       TravelInsurance  
count         1490.000  
mean             0.357  
std              0.479  
min              0.000  
25%              0.000  
50%              0.000  
75%              1.000  
max              1.000

In [13]:
test_df.describe().round(3)

Customer      Age  AnnualIncome  FamilyMembers  ChronicDiseases
count   497.000  497.000       497.000        497.000          497.000
mean   1739.000   29.600    947585.513          4.680            0.284
std     143.616    3.011    363581.819          1.513            0.451
min    1491.000   25.000    300000.000          2.000            0.000
25%    1615.000   28.000    650000.000          4.000            0.000
50%    1739.000   29.000    950000.000          4.000            0.000
75%    1863.000   32.000   1250000.000          6.000            1.000
max    1987.000   35.000   1750000.000          9.000            1.000

Las distribuciones del test set y el train set son muy similares

In [14]:
profile_train = ProfileReport(train_df)
profile_train

Summarize dataset:   0%|          | 0/23 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [15]:
profile_test = ProfileReport(test_df)
profile_test

Summarize dataset:   0%|          | 0/22 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Observando los valores y la distribución de las distintas variables podemos ver que tenemos:
- 4 variables binarias: GraduateOrNot, ChronicDiseases, FrequentFlyer, EverTravelledAbroad
- 1 categorica: Employment Type, con dos valores posibles, Private Sector/Self Employed o Government Sector
- 3 numericas: Age, AnnualIncome y FamilyMembers	
- La variable Customer no aporta información, si no que sirve para identificar a cada cliente

Sin embargo, las variables Age y FamilyMembers pueden considerarse como categoricas, Age con 11 posibles valores y  FamilyMembers con 8 posibles valores y esto es lo que vamos a hacer en el encoding.

## Encoding

La idea es dejar una única variable continua ('AnnualIncome'), y todo el resto tratarlas como categóricas y hacerles one-hot encoding

In [3]:
train_df = pd.read_csv("../data/travel_insurance_prediction_train.csv")
test_df = pd.read_csv("../data/travel_insurance_prediction_test.csv")

In [4]:
# Separamos la variable objetivo y tiramos la columna 'Customer' que no aporta información
y_train = train_df['TravelInsurance']
X_train = train_df.drop(columns=["Customer", "TravelInsurance"])

X_kaggle = test_df.drop(columns=["Customer"])

X_train.head()

Age               Employment Type GraduateOrNot  AnnualIncome  \
0   33  Private Sector/Self Employed           Yes        550000   
1   28  Private Sector/Self Employed           Yes        800000   
2   31  Private Sector/Self Employed           Yes       1250000   
3   31             Government Sector            No        300000   
4   28  Private Sector/Self Employed           Yes       1250000   

   FamilyMembers  ChronicDiseases FrequentFlyer EverTravelledAbroad  
0              6                0            No                  No  
1              7                0           Yes                  No  
2              4                0            No                  No  
3              7                0            No                  No  
4              3                0            No                  No

In [5]:
# One-hot de variables binarias
X_train.replace(to_replace={'Private Sector/Self Employed':1, 'Government Sector':0, 'Yes':1, 'No':0}, inplace=True)
X_train.rename(columns={'Employment Type':'PrivateSector/SelfEmployed'}, inplace=True)
X_kaggle.replace(to_replace={'Private Sector/Self Employed':1, 'Government Sector':0, 'Yes':1, 'No':0}, inplace=True)
X_kaggle.rename(columns={'Employment Type':'PrivateSector/SelfEmployed'}, inplace=True)

X_train.head()

Age  PrivateSector/SelfEmployed  GraduateOrNot  AnnualIncome  \
0   33                           1              1        550000   
1   28                           1              1        800000   
2   31                           1              1       1250000   
3   31                           0              0        300000   
4   28                           1              1       1250000   

   FamilyMembers  ChronicDiseases  FrequentFlyer  EverTravelledAbroad  
0              6                0              0                    0  
1              7                0              1                    0  
2              4                0              0                    0  
3              7                0              0                    0  
4              3                0              0                    0

In [6]:
# Paso Age y FamilyMembers a string para que el DictVectorizer las tome como categoricas y las one-hot encodee
X_train = X_train.astype({'Age':str, 'FamilyMembers':str})
X_kaggle = X_kaggle.astype({'Age':str, 'FamilyMembers':str})

In [7]:
# One-hot encoding de variables de más de dos categorias
feature_dict = list(X_train.T.to_dict().values()) 
from sklearn.feature_extraction import DictVectorizer
vec = DictVectorizer()
feature_matrix = vec.fit_transform(feature_dict)
dense_feature_matrix = feature_matrix.todense()
columns_encoding = vec.get_feature_names()
X_train = pd.DataFrame(dense_feature_matrix, columns=columns_encoding)
X_train

Age=25  Age=26  Age=27  Age=28  Age=29  Age=30  Age=31  Age=32  Age=33  \
0        0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     1.0   
1        0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0   
2        0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
3        0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
4        0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0   
...      ...     ...     ...     ...     ...     ...     ...     ...     ...   
1485     0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
1486     0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
1487     0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0   
1488     0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
1489     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0     0.0   

      Age=34  ...  FamilyMembers=3  FamilyMembers=4  FamilyMembers=5  \
0        0.0  ...              0.0              0.0              0.0   
1        0.0  ...              0.0              0.0              0.0   
2        0.0  ...              0.0              1.0              0.0   
3        0.0  ...              0.0              0.0              0.0   
4        0.0  ...              1.0              0.0              0.0   
...      ...  ...              ...              ...              ...   
1485     0.0  ...              0.0              0.0              1.0   
1486     0.0  ...              1.0              0.0              0.0   
1487     0.0  ...              0.0              0.0              1.0   
1488     0.0  ...              0.0              0.0              1.0   
1489     0.0  ...              0.0              1.0              0.0   

      FamilyMembers=6  FamilyMembers=7  FamilyMembers=8  FamilyMembers=9  \
0                 1.0              0.0              0.0              0.0   
1                 0.0              1.0              0.0              0.0   
2                 0.0              0.0              0.0              0.0   
3                 0.0              1.0              0.0              0.0   
4                 0.0              0.0              0.0              0.0   
...               ...              ...              ...              ...   
1485              0.0              0.0              0.0              0.0   
1486              0.0              0.0              0.0              0.0   
1487              0.0              0.0              0.0              0.0   
1488              0.0              0.0              0.0              0.0   
1489              0.0              0.0              0.0              0.0   

      FrequentFlyer  GraduateOrNot  PrivateSector/SelfEmployed  
0               0.0            1.0                         1.0  
1               1.0            1.0                         1.0  
2               0.0            1.0                         1.0  
3               0.0            0.0                         0.0  
4               0.0            1.0                         1.0  
...             ...            ...                         ...  
1485            0.0            0.0                         0.0  
1486            1.0            1.0                         1.0  
1487            0.0            1.0                         1.0  
1488            0.0            1.0                         0.0  
1489            0.0            0.0                         1.0  

[1490 rows x 25 columns]

In [8]:
feature_dict = list(X_kaggle.T.to_dict().values()) 
from sklearn.feature_extraction import DictVectorizer
vec = DictVectorizer()
feature_matrix = vec.fit_transform(feature_dict)
dense_feature_matrix = feature_matrix.todense()
columns_encoding = vec.get_feature_names()
X_kaggle = pd.DataFrame(dense_feature_matrix, columns=columns_encoding)
X_kaggle

Age=25  Age=26  Age=27  Age=28  Age=29  Age=30  Age=31  Age=32  Age=33  \
0       0.0     0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0   
1       0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0   
2       0.0     0.0     0.0     0.0     0.0     0.0     1.0     0.0     0.0   
3       0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0   
4       0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     1.0   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
492     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     1.0   
493     1.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
494     0.0     0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0   
495     1.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
496     0.0     0.0     1.0     0.0     0.0     0.0     0.0     0.0     0.0   

     Age=34  ...  FamilyMembers=3  FamilyMembers=4  FamilyMembers=5  \
0       0.0  ...              0.0              1.0              0.0   
1       0.0  ...              0.0              0.0              1.0   
2       0.0  ...              0.0              1.0              0.0   
3       0.0  ...              1.0              0.0              0.0   
4       0.0  ...              0.0              1.0              0.0   
..      ...  ...              ...              ...              ...   
492     0.0  ...              0.0              0.0              0.0   
493     0.0  ...              1.0              0.0              0.0   
494     0.0  ...              0.0              0.0              1.0   
495     0.0  ...              0.0              0.0              0.0   
496     0.0  ...              1.0              0.0              0.0   

     FamilyMembers=6  FamilyMembers=7  FamilyMembers=8  FamilyMembers=9  \
0                0.0              0.0              0.0              0.0   
1                0.0              0.0              0.0              0.0   
2                0.0              0.0              0.0              0.0   
3                0.0              0.0              0.0              0.0   
4                0.0              0.0              0.0              0.0   
..               ...              ...              ...              ...   
492              1.0              0.0              0.0              0.0   
493              0.0              0.0              0.0              0.0   
494              0.0              0.0              0.0              0.0   
495              0.0              0.0              0.0              0.0   
496              0.0              0.0              0.0              0.0   

     FrequentFlyer  GraduateOrNot  PrivateSector/SelfEmployed  
0              0.0            1.0                         1.0  
1              1.0            1.0                         1.0  
2              1.0            1.0                         0.0  
3              0.0            1.0                         1.0  
4              1.0            1.0                         1.0  
..             ...            ...                         ...  
492            0.0            1.0                         0.0  
493            0.0            0.0                         1.0  
494            0.0            1.0                         1.0  
495            0.0            1.0                         0.0  
496            0.0            1.0                         0.0  

[497 rows x 25 columns]

### Split y scaler

Dividimos en conjunto de train y test y estandarizamos

In [9]:
from sklearn.model_selection import train_test_split
X, X_test, y, y_test = train_test_split(X_train, y_train, stratify=y_train, test_size=0.1, random_state=20)

In [10]:
# Estandarizamos la variable continua 'AnnualIncome', ya que algunos algoritmos lo necesitan
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaler.fit(X['AnnualIncome'].values.reshape(-1, 1))
X_scaled = X.copy()
X_scaled['AnnualIncome'] = scaler.transform(X['AnnualIncome'].values.reshape(-1, 1))
X_test_scaled = X_test.copy()
X_test_scaled['AnnualIncome'] = scaler.transform(X_test['AnnualIncome'].values.reshape(-1, 1))
X_kaggle_scaled = X_kaggle.copy()
X_kaggle_scaled['AnnualIncome'] = scaler.transform(X_kaggle['AnnualIncome'].values.reshape(-1, 1))
y_scaled = y
y_test_scaled = y_test

# Es medio confuso pro acá el X_train es la data completa, sin dividir en nada
# Cuando elija el mejor modelo, despues lo quiero reentrenar con la data completa antes de predicir la de test
# Asi que tambien necesito la data completa escalada
scaler = StandardScaler()
scaler.fit(X_train['AnnualIncome'].values.reshape(-1, 1))
X_train_scaled = X_train.copy()
X_train_scaled['AnnualIncome'] = scaler.transform(X_train['AnnualIncome'].values.reshape(-1, 1))
y_train_scaled = y_train

### Baseline

In [31]:
# Definimos algunas funciones para no repetir codigo

# fitted_gs_cv tiene que ser el resultado de un gridsearch/randomized gridsearch + cross validation, 
# fitteado en un conjunto SIN interseccion con X_test, y_test
# OJO: si se fitteo con data escalada/estandarizada, la de test tambien tiene que tener la misma transformación

def best_model_metrics(fitted_gs_cv, X_test, y_test, class_report=True, conf_matrix=True, results=False, save=False, name='resultados', ret=False):
    best_model = fitted_gs_cv.best_estimator_
    best_params = fitted_gs_cv.best_params_
    best_score = fitted_gs_cv.best_score_
    y_pred = best_model.predict(X_test)
    print('F1 score promedio del modelo en train set:', best_score)
    print('F1 score en test set:', f1_score(y_test, y_pred))
    print('OJO: Si en el train set da mucho mayor, probablemente este overfitteando')
    print('\n Parametros:')
    print(best_params)
    if class_report:
        print('\n Classification Report:')
        print(classification_report(y_test, y_pred))
    if conf_matrix:
        print('\n Matriz de Confucion:')
        print(confusion_matrix(y_test, y_pred))
    if results:
        results = fitted_gs_cv.cv_results_
        df = pd.DataFrame(results)
        print('\n Resultados de los mejores 10 modelos:')
        print(df[df.rank_test_score<11].iloc[:,4:])
        if 'mean_train_score' in list(df.columns):
            df['dif_mean_train_test_score']=df['mean_train_score']-df['mean_test_score']
            print('\n Resultados de los 10 modelos con menor diferencia entre train y test:')
            df_top = df[df.rank_test_score<51].iloc[:,4:]
            print(df_top.sort_values('dif_mean_train_test_score').head(10)) 
        if save:
            df.to_csv(name)    
            
    if ret:
        ret = {'best_model': best_model, 'best_params': best_params, 'best_score': best_score, 'resultados': df}
    else:
        ret = None
    return ret

def score_train_test(model, X, y, X_test, y_test):
    model2 = clone(model)
    print('F1 score cross-validation:', np.mean(cross_val_score(model, X_scaled, y_scaled, cv=5, scoring='f1')))
    model2.fit(X, y)
    y_pred = model2.predict(X_test)
    print('F1 score test:', f1_score(y_test, y_pred))
            
def generar_submission(model, X_train, y_train, X_submission, test_df, name='submission.csv'):
    model.fit(X_train, y_train)
    test_id = test_df["Customer"]
    test_pred = model.predict(X_submission)
    submission = pd.DataFrame(list(zip(test_id, test_pred)), columns=["Customer", "TravelInsurance"])
    submission.to_csv(name, header=True, index=False)
    return len(submission)

In [12]:
# Código de los profes para generar el modelo de baseline
search_params = {
    'criterion': ['gini', 'entropy'],
    'min_samples_leaf': [1, 2, 5],
    'max_depth': [3, 6, 10]
}
tree = DecisionTreeClassifier(random_state=42)
tree_clf = GridSearchCV(tree, search_params, cv=5, scoring='f1', n_jobs=-1)
tree_clf.fit(X, y)

GridSearchCV(cv=5, estimator=DecisionTreeClassifier(random_state=42), n_jobs=-1,
             param_grid={'criterion': ['gini', 'entropy'],
                         'max_depth': [3, 6, 10],
                         'min_samples_leaf': [1, 2, 5]},
             scoring='f1')

In [13]:
best_model_metrics(tree_clf, X_test, y_test)

F1 score promedio del modelo en train set: 0.688411768252372
F1 score en test set: 0.6153846153846154
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'criterion': 'entropy', 'max_depth': 6, 'min_samples_leaf': 1}

 Classification Report:
              precision    recall  f1-score   support

           0       0.77      0.99      0.86        96
           1       0.96      0.45      0.62        53

    accuracy                           0.80       149
   macro avg       0.86      0.72      0.74       149
weighted avg       0.84      0.80      0.78       149


 Matriz de Confucion:
[[95  1]
 [29 24]]


### Varios modelos, con cross validation, sin grid search

Es para tener un baseline de cada modelo, se puede ver además a cuales les afecta el scaling y a cuales no

In [32]:
from sklearn.ensemble import RandomForestClassifier
forest = RandomForestClassifier(n_estimators=500, max_depth=5, max_features=5, random_state=30, n_jobs=-1)
print('RandomForestClassifier')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(forest, X, y, cv=5, scoring='f1'))))
forest = RandomForestClassifier(n_estimators=500, max_depth=5, max_features=5, random_state=30, n_jobs=-1)
print('RandomForestClassifier, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(forest, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.ensemble import GradientBoostingClassifier
gbrt = GradientBoostingClassifier(random_state=30)
print('GradientBoostingClassifier')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(gbrt, X, y, cv=5, scoring='f1'))))
gbrt = GradientBoostingClassifier(random_state=30)
print('GradientBoostingClassifier, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(gbrt, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=1)
print('KNeighborsClassifier, 1 neighbor')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(knn, X, y, cv=5, scoring='f1'))))
knn = KNeighborsClassifier(n_neighbors=1)
print('KNeighborsClassifier, 1 neighbor, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(knn, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=3)
print('KNeighborsClassifier, 3 neighbors')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(knn, X, y, cv=5, scoring='f1'))))
knn = KNeighborsClassifier(n_neighbors=3)
print('KNeighborsClassifier, 3 neighbors, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(knn, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.linear_model import LogisticRegression
logreg = LogisticRegression(max_iter=1000)
print('LogisticRegression')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(logreg, X, y, cv=5, scoring='f1'))))
logreg = LogisticRegression(max_iter=1000)
print('LogisticRegression, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(logreg, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.svm import SVC
svm = SVC(kernel='rbf', C=10, gamma=0.1)
print('SVC')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(svm, X, y, cv=5, scoring='f1'))))
svm = SVC(kernel='rbf', C=10, gamma=0.1)
print('SVC, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(svm, X_scaled, y_scaled, cv=5, scoring='f1'))))

from sklearn.svm import SVC
svm = SVC(kernel='poly', degree=2, C=1, gamma="scale")
print('SVC')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(svm, X, y, cv=5, scoring='f1'))))
svm = SVC(kernel='poly', degree=2, C=1, gamma="scale")
print('SVC, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(svm, X_scaled, y_scaled, cv=5, scoring='f1'))))

import xgboost as xgb
xgb_estimator = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss')
print('xgb')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(xgb_estimator, X, y, cv=5, scoring='f1'))))
xgb_estimator = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss')
print('xgb, scaled')
print("f1 score, clase positiva, cv: {:.3f}".format(np.mean(cross_val_score(xgb_estimator, X_scaled, y_scaled, cv=5, scoring='f1'))))

RandomForestClassifier
f1 score, clase positiva, cv: 0.617
RandomForestClassifier, scaled
f1 score, clase positiva, cv: 0.617
GradientBoostingClassifier
f1 score, clase positiva, cv: 0.699
GradientBoostingClassifier, scaled
f1 score, clase positiva, cv: 0.699
KNeighborsClassifier, 1 neighbor
f1 score, clase positiva, cv: 0.626
KNeighborsClassifier, 1 neighbor, scaled
f1 score, clase positiva, cv: 0.625
KNeighborsClassifier, 3 neighbors
f1 score, clase positiva, cv: 0.658
KNeighborsClassifier, 3 neighbors, scaled
f1 score, clase positiva, cv: 0.659
LogisticRegression
f1 score, clase positiva, cv: 0.000
LogisticRegression, scaled
f1 score, clase positiva, cv: 0.634
SVC
f1 score, clase positiva, cv: 0.641
SVC, scaled
f1 score, clase positiva, cv: 0.700
SVC
f1 score, clase positiva, cv: 0.602
SVC, scaled
f1 score, clase positiva, cv: 0.679
xgb
f1 score, clase positiva, cv: 0.662
xgb, scaled
f1 score, clase positiva, cv: 0.662


In [61]:
from pycaret.classification import *

clf = setup(train_df, target='TravelInsurance')
#esta libreria compara varios modelos y te dice en teoria cual es el mejor
compare_models()

GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                           learning_rate=0.1, loss='deviance', max_depth=3,
                           max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_impurity_split=None,
                           min_samples_leaf=1, min_samples_split=2,
                           min_weight_fraction_leaf=0.0, n_estimators=100,
                           n_iter_no_change=None, presort='deprecated',
                           random_state=2152, subsample=1.0, tol=0.0001,
                           validation_fraction=0.1, verbose=0,
                           warm_start=False)

### SVM - Hiperparameter tunning

In [28]:
# Probé todos los kernels y muchos valores de C y los mejores fueron 'poly' y 'rbf', C entre 1 y 10. 
# Ahora pruebo también otros paramentros
# Para SVM es importante que la data este estandarizada

param_grid_svm = [
    {'C': [1, 3, 10],
    'kernel': ['poly'],
    'degree': [2, 3, 4],
    'gamma': ['scale', 'auto'] + [0.001, 0.01, 0.1, 1],
    'class_weight': ['balanced', None]},
    {'C': [1, 3, 10],
    'kernel': ['rbf'],
    'gamma': ['scale', 'auto'] + [0.001, 0.01, 0.1, 1],
    'class_weight': ['balanced', None]}    
]

In [26]:
model_svm = SVC(random_state=0)

#gs_cv_svm = GridSearchCV(model_svm, param_grid_svm, scoring='f1', cv=5)
#gs_cv_svm.fit(X_scaled, y_scaled)

In [27]:
#resultados_svm = best_model_metrics(gs_cv_svm, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_svm_2', ret=True)

F1 score promedio del modelo en train set: 0.7001466372367953
F1 score en test set: 0.6666666666666666
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'C': 3, 'class_weight': None, 'degree': 2, 'gamma': 'scale', 'kernel': 'poly'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.97      0.87        96
           1       0.90      0.53      0.67        53

    accuracy                           0.81       149
   macro avg       0.85      0.75      0.77       149
weighted avg       0.83      0.81      0.80       149


 Matriz de Confucion:
[[93  3]
 [25 28]]

 Resultados de los mejores 10 modelos:
     mean_fit_time  std_fit_time  mean_score_time  std_score_time param_C  \
0         0.045885      0.004606         0.008177        0.000397       1   
24        0.042682      0.005699         0.007377        0.000487       1   
54        0.065821      0.010038         0.006984        0.000019

Los puestos 2 a 5 son de rbf, asi que intento optimizar mejor ese

In [52]:
C_values = list(np.logspace(-1, 3, 9))
gamma_values = list(np.logspace(-2, 0, 5))

param_grid_svm = {
    'C': C_values,
    'kernel': ['rbf'],
    'gamma': ['scale', 'auto'] + gamma_values,
    'class_weight': ['balanced', None]
}    

In [53]:
model_svm = SVC(random_state=0)

#gs_cv_svm = GridSearchCV(model_svm, param_grid_svm, scoring='f1', cv=5, verbose=2, return_train_score=True)
#gs_cv_svm.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 126 candidates, totalling 630 fits
[CV] END C=0.1, class_weight=balanced, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END C=0.1, class_weight=b

[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=ba

[CV] END ...C=1.0, class_weight=None, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=auto, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END ...C=1.0, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END C=1.0, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=1.0, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV]

[CV] END C=3.1622776601683795, class_weight=None, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, gamma=1.0, kernel=rbf; total time=   0.0s


[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.01, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.03162277660168379, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced, gamma=0.1, kernel=rbf; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=balanced,

[CV] END C=100.0, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=0.31622776601683794, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=balanced, gamma=1.0, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=None, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=None, gamma=scale, kernel=rbf; total time=   0.1s
[CV] END C=100.0, class_weight=None, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=None, gamma=scale, kernel=rbf; total time=   0.0s
[CV] END C=100.0, class_weight=None, gamma=scale, kernel=rbf; t

[CV] END C=316.22776601683796, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.01, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.2s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.03162277660168379, kernel=rbf; total time=   0.2s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.1, kernel=rbf; total time=   0.1s
[CV] END C=316.22776601683796, class_weight=None, gamma=0.1, kernel=rbf; total time=   0.

[CV] END .C=1000.0, class_weight=None, gamma=1.0, kernel=rbf; total time=   0.1s
[CV] END .C=1000.0, class_weight=None, gamma=1.0, kernel=rbf; total time=   0.1s


GridSearchCV(cv=5, estimator=SVC(random_state=0),
             param_grid={'C': [0.1, 0.31622776601683794, 1.0,
                               3.1622776601683795, 10.0, 31.622776601683793,
                               100.0, 316.22776601683796, 1000.0],
                         'class_weight': ['balanced', None],
                         'gamma': ['scale', 'auto', 0.01, 0.03162277660168379,
                                   0.1, 0.31622776601683794, 1.0],
                         'kernel': ['rbf']},
             return_train_score=True, scoring='f1', verbose=2)

In [57]:
#resultados_svm = best_model_metrics(gs_cv_svm, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_svm4_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7054889898801024
F1 score en test set: 0.6823529411764705
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'C': 100.0, 'class_weight': None, 'gamma': 0.03162277660168379, 'kernel': 'rbf'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.97      0.87        96
           1       0.91      0.55      0.68        53

    accuracy                           0.82       149
   macro avg       0.85      0.76      0.78       149
weighted avg       0.83      0.82      0.81       149


 Matriz de Confucion:
[[93  3]
 [24 29]]

 Resultados de los mejores 10 modelos:
     mean_fit_time  std_fit_time  mean_score_time  std_score_time     param_C  \
40        0.053227      0.006094         0.027937        0.003012         1.0   
67        0.071614      0.009958         0.026134        0.002721        10.0   
71        0.079631      0.005128         0.027321  

In [50]:
# Mejor svm
svm1 = SVC(kernel='rbf', C=100, gamma=0.0316)

score_train_test(svm1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7046132634252024
F1 score test: 0.6823529411764705


In [58]:
generar_submission(svm1, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_svm1_reentrenado.csv')

497

### XGB - Hiperparameter tunning

In [ ]:
param_grid_xgb_random = {
    'max_depth': list(np.arange(1, 12)),
    'n_estimators': list(np.arange(100, 1001, 100)),
    'learning_rate': list(np.arange(0.1, 0.41, 0.1)),
    'colsample_bytree': list(np.linspace(0.5, 1, 6)),
    'subsample': list(np.linspace(0.6, 1, 5))
}

In [ ]:
model =  xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0)

#rgs_cv_xgb = RandomizedSearchCV(estimator=model, param_distributions=param_grid_xgb_random, n_iter=500, scoring='f1', cv=5, verbose=2, random_state=0)
#rgs_cv_xgb.fit(X_scaled, y_scaled)

In [ ]:
#best_model_metrics(rgs_cv_xgb, X_test_scaled, y_test_scaled, results=True)

In [34]:
# Mejor del random gridsearch
xgb3 = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0, 
                         subsample=0.9, n_estimators=300, max_depth=2, learning_rate=0.2, colsample_bytree=0.7)

score_train_test(xgb3, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7047519014698302
F1 score test: 0.6976744186046512


In [29]:
param_grid_xgb = {
    'max_depth': list(np.arange(1, 3)),
    'n_estimators': list(np.arange(100, 701, 100)),
    'learning_rate': [0.1, 0.2],
    'colsample_bytree': [0.7, 0.75, 0.8],
    'subsample': list(np.linspace(0.8, 1, 3))
}

In [30]:
model =  xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0)

#gs_cv_xgb = GridSearchCV(estimator=model, param_grid=param_grid_xgb, scoring='f1', cv=5, verbose=2, return_train_score=True)
#gs_cv_xgb.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 252 candidates, totalling 1260 fits
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsamp

[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=500, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=500, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=500, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=500, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=1, n_estimators=600,

[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=300, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=400, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=0.7, learning_rate=0.1, max_depth=2, n_estimators=400,

[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=1.0; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=1.0; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100, subsample=1.0; total time=   0.0s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=100,

[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, learning_rate=0.2, max_depth=1, n_estimators=600,

...

[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=400, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=400, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=400, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=400, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.6s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=0.8, learning_rate=0.1, max_depth=2, n_estimators=500,

[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=1.0; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=1.0; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=1.0; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=1.0; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=200, subsample=1.0; total time=   0.1s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=300, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=300,

[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=1.0; total time=   0.4s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=1.0; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700, subsample=1.0; total time=   0.4s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=1, n_estimators=700,

[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.8, learning_rate=0.2, max_depth=2, n_estimators=500,

GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     eval_metric='logloss', gamma=None,
                                     gpu_id=None, importance_type='gain',
                                     interaction_constraints=None,
                                     learning_rate=None, max_delta_step=None,
                                     max_depth=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     n...
                                     reg_alpha=None, reg_lambda=None,
                                     scale_pos_weight=None, subsample=None,
                                     tree_method=None, use_label_encoder=False,
                    

In [58]:
#resultados_xgb = best_model_metrics(gs_cv_xgb, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_xgb3_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7098666557635498
F1 score en test set: 0.6506024096385542
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'colsample_bytree': 0.75, 'learning_rate': 0.1, 'max_depth': 2, 'n_estimators': 500, 'subsample': 0.9}

 Classification Report:
              precision    recall  f1-score   support

           0       0.78      0.97      0.87        96
           1       0.90      0.51      0.65        53

    accuracy                           0.81       149
   macro avg       0.84      0.74      0.76       149
weighted avg       0.82      0.81      0.79       149


 Matriz de Confucion:
[[93  3]
 [26 27]]

 Resultados de los mejores 10 modelos:
     mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
33        0.491884      0.003858         0.007181    3.991130e-04   
34        0.493680      0.009913         0.007181    3.987553e-04   
36        0.600793      0.030169         0.007381    4.882862e-04

In [35]:
# Mejor del gridsearch
xgb1 = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0, 
                         subsample=0.9, n_estimators=500, max_depth=2, learning_rate=0.1, colsample_bytree=0.75)

score_train_test(xgb1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7098666557635498
F1 score test: 0.6506024096385542


In [36]:
# Mejor del gridsearch con mas learning_rate
xgb2 = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0, 
                         subsample=0.9, n_estimators=500, max_depth=2, learning_rate=0.2, colsample_bytree=0.75)

score_train_test(xgb2, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6952521357108024
F1 score test: 0.6896551724137931


Ahora voy a jugar un poco con los parametros de regularización

In [103]:
param_grid_xgb = {
    'max_depth': [2],
    'subsample': [0.9],
    'n_estimators': [300, 500],
    'learning_rate': [0.1, 0.2],
    'colsample_bytree': [0.7, 0.75],
    'gamma': [0, 1, 2],
    'reg_alpha': [0.0001, 0.001, 0.01, 0.1, 1],
    'reg_lambda': [0.0001, 0.001, 0.01, 0.1, 1], 
}

In [104]:
model =  xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0)

#gs_cv_xgb = GridSearchCV(estimator=model, param_grid=param_grid_xgb, scoring='f1', cv=5, verbose=2, return_train_score=False)
#gs_cv_xgb.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 600 candidates, totalling 3000 fits
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.0001, reg_lambda=0.001, subsa

[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.0001, subsample=0.9; total time=   0.3s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.0001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.0001, subsample=0.9; total time=   0.3s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=0.01, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_

[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.001, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=300, reg_alpha=1, reg_lambda=0.01, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2,

[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.001, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.001, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.001, reg_lambda=0.01, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.7, gamma=0, learning_r

[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.01, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_dep

...

[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.3s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.3s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=0.1, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=1, subsample=0.9; total time=   0.3s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=300, reg_alpha=0.1, reg_lambda=1, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_dept

[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=0.1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.0001, reg_lambda=1, subsample=0.9; total time=   0.5s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0

[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.01, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.01, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.01, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.01, reg_lambda=1, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.0001, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=0.1, reg_lambda=0.0001, subsample=0.9; total time=   0.4s
[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, ma

[CV] END colsample_bytree=0.75, gamma=2, learning_rate=0.2, max_depth=2, n_estimators=500, reg_alpha=1, reg_lambda=1, subsample=0.9; total time=   0.4s


GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     eval_metric='logloss', gamma=None,
                                     gpu_id=None, importance_type='gain',
                                     interaction_constraints=None,
                                     learning_rate=None, max_delta_step=None,
                                     max_depth=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     n...
                                     scale_pos_weight=None, subsample=None,
                                     tree_method=None, use_label_encoder=False,
                                     validate_parameters=None, verbosity=None),
          

In [109]:
#resultados_xgb2 = best_model_metrics(gs_cv_xgb, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_xgb5_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7128818361167725
F1 score en test set: 0.6506024096385542
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'colsample_bytree': 0.75, 'gamma': 1, 'learning_rate': 0.1, 'max_depth': 2, 'n_estimators': 500, 'reg_alpha': 0.0001, 'reg_lambda': 0.01, 'subsample': 0.9}

 Classification Report:
              precision    recall  f1-score   support

           0       0.78      0.97      0.87        96
           1       0.90      0.51      0.65        53

    accuracy                           0.81       149
   macro avg       0.84      0.74      0.76       149
weighted avg       0.82      0.81      0.79       149


 Matriz de Confucion:
[[93  3]
 [26 27]]

 Resultados de los mejores 10 modelos:
    param_colsample_bytree param_gamma param_learning_rate param_max_depth  \
0                      0.7           0                 0.1               2   
168                    0.7           1                 0.2     

In [37]:
# Mejor del gridsearch1 con parametros de regularización
xgb4 = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0, 
                         subsample=0.9, n_estimators=300, max_depth=2, learning_rate=0.2, colsample_bytree=0.7, 
                         gamma=1, reg_alpha=0.1, reg_lambda=0.1)

score_train_test(xgb4, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7097027987071336
F1 score test: 0.7126436781609194


In [38]:
# Mejor del gridsearch2 con parametros de regularización pero mas learning rate
xgb5 = xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=0, 
                         subsample=0.9, n_estimators=500, max_depth=2, learning_rate=0.2, colsample_bytree=0.75, 
                         gamma=1, reg_alpha=0.0001, reg_lambda=0.01)

score_train_test(xgb5, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.703175120582383
F1 score test: 0.6976744186046512


In [57]:
generar_submission(xgb4, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_xgb4_reentrenado.csv')

497

### Regresión Logística - Hiperparameter tunning

In [75]:
C_values_lr = list(np.logspace(-2, 2.5, 10))

param_grid_lr = [
    {'C': C_values_lr,
    'penalty': ['l2'],
    'class_weight': ['balanced', None],
    'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga']},
    {'penalty': ['none'],
    'class_weight': ['balanced', None],
    'solver': ['newton-cg', 'lbfgs', 'sag', 'saga']},
    {'C': C_values_lr,
    'penalty': ['l1'],
    'class_weight': ['balanced', None],
    'solver': ['liblinear', 'saga']},
    {'C': C_values_lr,
    'penalty': ['elasticnet'],
    'class_weight': ['balanced', None],
    'l1_ratio': [0.2, 0.4, 0.6, 0.8],
    'solver': ['saga']}
]     

In [76]:
model_lr = LogisticRegression(random_state=0, max_iter=300)

gs_cv_lr = GridSearchCV(model_lr, param_grid_lr, scoring='f1', cv=5, verbose=2)
gs_cv_lr.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 228 candidates, totalling 1140 fits
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.01, class_weight=balanced, penalty=l2, solver=libline

[CV] END C=0.03162277660168379, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=0.1, class_weight=balanced, penalt

[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=0.31622776601683794, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=1.0, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=1.0, class_weight=balanced, penalty=l2, solver=newton-cg; total time=   0.0s
[CV] END C=1.0, class_weight=balanced, penalty=l2, solver=newton-cg

[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2, solver=saga; total time=   0.0s
[CV] END C=3.1622776601683795, class_weight=None, penalty=l2

[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=lbfgs; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=liblinear; total time=   0.0s
[CV] END C=31.622776601683793, class_weight=None, penalty=l2, solver=sag; total time=   0.0s
[CV] END C=31.622776601683793, c

...

c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "


[CV] END C=100.0, class_weight=None, l1_ratio=0.6, penalty=elasticnet, solver=saga; total time=   0.1s
[CV] END C=100.0, class_weight=None, l1_ratio=0.6, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=100.0, class_weight=None, l1_ratio=0.6, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=100.0, class_weight=None, l1_ratio=0.8, penalty=elasticnet, solver=saga; total time=   0.0s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "


[CV] END C=100.0, class_weight=None, l1_ratio=0.8, penalty=elasticnet, solver=saga; total time=   0.1s
[CV] END C=100.0, class_weight=None, l1_ratio=0.8, penalty=elasticnet, solver=saga; total time=   0.1s
[CV] END C=100.0, class_weight=None, l1_ratio=0.8, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=100.0, class_weight=None, l1_ratio=0.8, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=316.22776601683796, class_weight=balanced, l1_ratio=0.2, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=316.22776601683796, class_weight=balanced, l1_ratio=0.2, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=316.22776601683796, class_weight=balanced, l1_ratio=0.2, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=316.22776601683796, class_weight=balanced, l1_ratio=0.2, penalty=elasticnet, solver=saga; total time=   0.0s
[CV] END C=316.22776601683796, class_weight=balanced, l1_ratio=0.2, penalty=elasticnet, solver=saga; total t

GridSearchCV(cv=5, estimator=LogisticRegression(max_iter=300, random_state=0),
             param_grid=[{'C': [0.01, 0.03162277660168379, 0.1,
                                0.31622776601683794, 1.0, 3.1622776601683795,
                                10.0, 31.622776601683793, 100.0,
                                316.22776601683796],
                          'class_weight': ['balanced', None], 'penalty': ['l2'],
                          'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag',
                                     'saga']},
                         {'class_weight': ['balanced'...
                                316.22776601683796],
                          'class_weight': ['balanced', None], 'penalty': ['l1'],
                          'solver': ['liblinear', 'saga']},
                         {'C': [0.01, 0.03162277660168379, 0.1,
                                0.31622776601683794, 1.0, 3.1622776601683795,
                                10.0, 31.622776601683793, 100

In [77]:
resultados_lr = best_model_metrics(gs_cv_lr, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_lr1_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.6450463937404823
F1 score en test set: 0.6542056074766356
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'C': 1.0, 'class_weight': 'balanced', 'penalty': 'l1', 'solver': 'liblinear'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.81      0.80      0.81        96
           1       0.65      0.66      0.65        53

    accuracy                           0.75       149
   macro avg       0.73      0.73      0.73       149
weighted avg       0.75      0.75      0.75       149


 Matriz de Confucion:
[[77 19]
 [18 35]]

 Resultados de los mejores 10 modelos:
      param_C param_class_weight param_penalty param_solver param_l1_ratio  \
30   0.316228           balanced            l2    newton-cg            NaN   
31   0.316228           balanced            l2        lbfgs            NaN   
32   0.316228           balanced            l2    liblinear    

In [39]:
# Mejor del gridsearch
lr1 = LogisticRegression(random_state=0, max_iter=300, C=1, class_weight='balanced', penalty='l1', solver='liblinear')

score_train_test(lr1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6450463937404823
F1 score test: 0.6542056074766356


### KNN - Hiperparameter tunning

In [15]:
param_grid_knn = {
    'n_neighbors' : list(np.arange(1, 31)),
     'weights' : ['uniform', 'distance'] ,
     'metric':   ['euclidean', 'manhattan']
}

In [18]:
model_knn = KNeighborsClassifier()

gs_cv_knn = GridSearchCV(model_knn, param_grid_knn, scoring='f1', cv=5, verbose=1, return_train_score=True)
gs_cv_knn.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 120 candidates, totalling 600 fits


GridSearchCV(cv=5, estimator=KNeighborsClassifier(),
             param_grid={'metric': ['euclidean', 'manhattan'],
                         'n_neighbors': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12,
                                         13, 14, 15, 16, 17, 18, 19, 20, 21, 22,
                                         23, 24, 25, 26, 27, 28, 29, 30],
                         'weights': ['uniform', 'distance']},
             return_train_score=True, scoring='f1', verbose=1)

In [19]:
resultados_knn = best_model_metrics(gs_cv_knn, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_knn_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.6791527922593213
F1 score en test set: 0.6521739130434783
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'metric': 'manhattan', 'n_neighbors': 5, 'weights': 'uniform'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.91      0.84        96
           1       0.77      0.57      0.65        53

    accuracy                           0.79       149
   macro avg       0.78      0.74      0.75       149
weighted avg       0.78      0.79      0.78       149


 Matriz de Confucion:
[[87  9]
 [23 30]]

 Resultados de los mejores 10 modelos:
    param_metric param_n_neighbors param_weights  \
8      euclidean                 5       uniform   
64     manhattan                 3       uniform   
68     manhattan                 5       uniform   
72     manhattan                 7       uniform   
73     manhattan                 7      distance   


In [40]:
# Mejor del gridsearch1
knn1 = KNeighborsClassifier(n_neighbors=5,metric='manhattan',weights='uniform')

score_train_test(knn1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6791527922593213
F1 score test: 0.6521739130434783


In [88]:
param_grid_knn2 = {
    'n_neighbors': neighbors,
    'weights': ['uniform'],
    'algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute'],
    'leaf_size': [5, 10, 15, 20, 25, 30, 35, 40, 45, 50]
}

In [89]:
model_knn2 = KNeighborsClassifier()

gs_cv_knn2 = GridSearchCV(model_knn2, param_grid_knn2, scoring='f1', cv=5, verbose=2)
gs_cv_knn2.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 400 candidates, totalling 2000 fits
[CV] END algorithm=auto, leaf_size=5, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=5, n_neighb

[CV] END algorithm=auto, leaf_size=10, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=10, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=10, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=10, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=1, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=15, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] E

[CV] END algorithm=auto, leaf_size=20, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=9, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=9, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=9, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=9, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=9, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=20, n_neighbors=10, weights=uniform; total time=   0.0s
[CV] E

[CV] END algorithm=auto, leaf_size=30, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=30, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END a

[CV] END algorithm=auto, leaf_size=40, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END algorithm=auto, leaf_size=40, n_neighbors=8, weights=uniform; total time=   0.0s
[CV] END a

...

[CV] END algorithm=brute, leaf_size=20, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=7, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=20, n_neighbors=7, weights=uniform; total time=   0.0s

[CV] END algorithm=brute, leaf_size=30, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=6, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=30, n_neighbors=6, weights=uniform; total time=   0.0s

[CV] END algorithm=brute, leaf_size=40, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=4, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=5, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=40, n_neighbors=5, weights=uniform; total time=   0.0s

[CV] END algorithm=brute, leaf_size=50, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=2, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=3, weights=uniform; total time=   0.0s
[CV] END algorithm=brute, leaf_size=50, n_neighbors=4, weights=uniform; total time=   0.0s

GridSearchCV(cv=5, estimator=KNeighborsClassifier(),
             param_grid={'algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute'],
                         'leaf_size': [5, 10, 15, 20, 25, 30, 35, 40, 45, 50],
                         'n_neighbors': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
                         'weights': ['uniform']},
             scoring='f1', verbose=2)

In [90]:
resultados_knn2 = best_model_metrics(gs_cv_knn2, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_knn2_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.6829838332161831
F1 score en test set: 0.6530612244897959
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'algorithm': 'kd_tree', 'leaf_size': 5, 'n_neighbors': 5, 'weights': 'uniform'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.80      0.86      0.83        96
           1       0.71      0.60      0.65        53

    accuracy                           0.77       149
   macro avg       0.75      0.73      0.74       149
weighted avg       0.77      0.77      0.77       149


 Matriz de Confucion:
[[83 13]
 [21 32]]

 Resultados de los mejores 10 modelos:
    param_algorithm param_leaf_size param_n_neighbors param_weights  \
132       ball_tree              20                 3       uniform   
134       ball_tree              20                 5       uniform   
142       ball_tree              25                 3       uniform   
144       b

In [41]:
# Mejor del gridsearch2
knn2 = KNeighborsClassifier(algorithm='kd_tree', leaf_size=5, n_neighbors=5, weights='uniform')

score_train_test(knn2, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6829838332161831
F1 score test: 0.6530612244897959


### ADA BOOST CLASSIFIER - Hiperparameter tunning

In [21]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.model_selection import RepeatedStratifiedKFold

model = AdaBoostClassifier()
grid = dict()
grid['n_estimators'] = [10, 50, 100, 500]
grid['learning_rate'] = [0.0001, 0.001, 0.01, 0.1, 1.0]
# define the evaluation procedure
#cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=3, random_state=1)
# define the grid search procedure
grid_search = GridSearchCV(estimator=model, param_grid=grid, n_jobs=-1, cv=5)
# execute the grid search

In [22]:
grid_result = grid_search.fit(X_scaled,y_scaled)

In [23]:
resultados_ada = best_model_metrics(grid_result, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_ada_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.8053653664761693
F1 score en test set: 0.6
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'learning_rate': 1.0, 'n_estimators': 100}

 Classification Report:
              precision    recall  f1-score   support

           0       0.76      0.97      0.85        96
           1       0.89      0.45      0.60        53

    accuracy                           0.79       149
   macro avg       0.83      0.71      0.73       149
weighted avg       0.81      0.79      0.76       149


 Matriz de Confucion:
[[93  3]
 [29 24]]

 Resultados de los mejores 10 modelos:
   param_learning_rate param_n_estimators  \
0               0.0001                 10   
1               0.0001                 50   
2               0.0001                100   
3               0.0001                500   
4                0.001                 10   
5                0.001                 50   
6                0.001          

In [42]:
# Mejor del gridsearch2
ada_1 = AdaBoostClassifier(learning_rate= 1.0, n_estimators= 100)

score_train_test(ada_1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6555966419750512
F1 score test: 0.6


### Random Forest - Hiperparameter tunning

In [99]:
param_grid_rf = {
    'max_depth': list(np.arange(3, 10)),
    'n_estimators': list(np.arange(100, 901, 100)),
    'min_samples_leaf': [1, 2, 3, 4],
    'criterion': ['gini', 'entropy']
}

In [100]:
model =  RandomForestClassifier(random_state=0)

gs_cv_rf = GridSearchCV(estimator=model, param_grid=param_grid_rf, scoring='f1', cv=5, verbose=2)
gs_cv_rf.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 504 candidates, totalling 2520 fits
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=200; total time=   0.3s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=200; total time=   0.3s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=200; total time=   0.3s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=200; total time=   0.2s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=1, n_estimators=200; total

[CV] END criterion=gini, max_depth=3, min_samples_leaf=2, n_estimators=900; total time=   1.5s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=2, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=2, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=2, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=3, n_estimators=200; total time=   0.2s
[CV] END criterion=gini, max_depth=3, min_samples_

[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=800; total time=   1.2s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=800; total time=   1.2s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=900; total time=   1.3s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=900; total time=   1.3s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=3, min_samples_leaf=4, n_estimators=900; total time=   1.4s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=1, n_estimators=100; total time=   0.1s
[CV] END criterion=gini, max_depth=4, min_samples_

[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=800; total time=   1.3s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=800; total time=   1.4s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=800; total time=   1.5s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=800; total time=   1.3s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=800; total time=   2.0s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=900; total time=   1.9s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=900; total time=   2.1s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=900; total time=   1.6s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=900; total time=   1.5s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=2, n_estimators=900; total time=   1.7s
[CV] END criterion=gini, max_depth=4, min_samples_

[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=700; total time=   1.2s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=700; total time=   1.4s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=700; total time=   1.4s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=800; total time=   1.6s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=800; total time=   1.4s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=800; total time=   1.5s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=800; total time=   1.7s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=800; total time=   1.6s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=900; total time=   1.7s
[CV] END criterion=gini, max_depth=4, min_samples_leaf=4, n_estimators=900; total time=   1.6s
[CV] END criterion=gini, max_depth=4, min_samples_

...

[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=500; total time=   1.0s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=500; total time=   0.9s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=500; total time=   0.9s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=600; total time=   1.1s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=600; total time=   1.1s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=600; total time=   1.2s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=600; total time=   1.1s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=600; total time=   1.1s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=700; total time=   1.3s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=2, n_estimators=700; total time=   1.3s
[CV] END criterion=e

[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=500; total time=   1.0s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=500; total time=   1.0s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=500; total time=   0.9s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=500; total time=   0.9s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=500; total time=   1.0s
[CV] END criterion=entropy, max_depth=8, min_samples_leaf=4, n_estimators=600; total time=   1.3s
[CV] END criterion=e

[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=400; total time=   0.7s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=2, n_estimators=400; total time=   0.7s
[CV] END criterion=e

[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=100; total time=   0.2s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=200; total time=   0.3s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=200; total time=   0.3s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=200; total time=   0.3s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=200; total time=   0.3s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=200; total time=   0.3s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=300; total time=   0.5s
[CV] END criterion=entropy, max_depth=9, min_samples_leaf=4, n_estimators=300; total time=   0.5s
[CV] END criterion=e

GridSearchCV(cv=5, estimator=RandomForestClassifier(random_state=0),
             param_grid={'criterion': ['gini', 'entropy'],
                         'max_depth': [3, 4, 5, 6, 7, 8, 9],
                         'min_samples_leaf': [1, 2, 3, 4],
                         'n_estimators': [100, 200, 300, 400, 500, 600, 700,
                                          800, 900]},
             scoring='f1', verbose=2)

In [101]:
resultados_rf = best_model_metrics(gs_cv_rf, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_rf1_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.6927524633041623
F1 score en test set: 0.6585365853658537
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'criterion': 'gini', 'max_depth': 9, 'min_samples_leaf': 2, 'n_estimators': 600}

 Classification Report:
              precision    recall  f1-score   support

           0       0.78      0.98      0.87        96
           1       0.93      0.51      0.66        53

    accuracy                           0.81       149
   macro avg       0.86      0.74      0.76       149
weighted avg       0.84      0.81      0.80       149


 Matriz de Confucion:
[[94  2]
 [26 27]]

 Resultados de los mejores 10 modelos:
    param_criterion param_max_depth param_min_samples_leaf param_n_estimators  \
223            gini               9                      1                800   
224            gini               9                      1                900   
228            gini               9                

In [43]:
# Mejor del gridsearch
rf1= RandomForestClassifier(random_state=0, min_samples_leaf=2, n_estimators=600, max_depth=9, criterion='gini')

score_train_test(rf1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.6927524633041623
F1 score test: 0.6585365853658537


### Gradient Bosting - Hiperparameter tunning

In [103]:
param_grid_gb_random = {
    'max_depth': [1, 2, 3, 4, 5, 6],
    'n_estimators': [50, 100, 200, 300, 400, 500],
    'learning_rate': [0.05, 0.1, 0.2, 0.3, 0.4],
    'subsample': list(np.linspace(0.6, 1, 5)),
    'criterion': ['friedman_mse', 'mse'],
    'min_samples_leaf': [1, 2, 3],
    'loss': ['deviance', 'exponential']
}

In [104]:
model =  GradientBoostingClassifier(random_state=0)

rgs_cv_gb = RandomizedSearchCV(estimator=model, param_distributions=param_grid_gb_random, n_iter=200, scoring='f1', cv=5, verbose=2, random_state=0)
rgs_cv_gb.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 200 candidates, totalling 1000 fits
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END criterion=friedman_mse, learning_rate=0.1, lo

[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=5, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.0s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=5, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.0s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=5, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.0s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=5, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.0s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=2, n_estimators=200, subsample=0.9; total time=   0.6s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=2, n_estimators=200, subsample=0.9; total time=   0.6s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=2, n_estimators=200, s

[CV] END criterion=mse, learning_rate=0.3, loss=deviance, max_depth=3, min_samples_leaf=3, n_estimators=50, subsample=0.8; total time=   0.0s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=4, min_samples_leaf=2, n_estimators=100, subsample=0.8; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=4, min_samples_leaf=2, n_estimators=100, subsample=0.8; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=4, min_samples_leaf=2, n_estimators=100, subsample=0.8; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=4, min_samples_leaf=2, n_estimators=100, subsample=0.8; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=4, min_samples_leaf=2, n_estimators=100, subsample=0.8; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.1, loss=deviance, max_depth=1, min

[CV] END criterion=mse, learning_rate=0.2, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.7s
[CV] END criterion=mse, learning_rate=0.2, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.8s
[CV] END criterion=mse, learning_rate=0.2, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.8s
[CV] END criterion=mse, learning_rate=0.2, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.7s
[CV] END criterion=mse, learning_rate=0.2, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.8s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=100, subsample=0.8; total time=   0.0s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=100, subsample=0.8; total time=   0.

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=200, subsample=0.9; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=200, subsample=0.9; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=200, subsample=0.9; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=6, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   1.0s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=6, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   1.0s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=6, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   1.0s
[CV] END criterion=mse, learning_rate=0.05, loss=deviance, max_depth=6, min_samples_leaf=3, n_estimators=400, subsample=0.7; total

...

[CV] END criterion=friedman_mse, learning_rate=0.3, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=200, subsample=0.7; total time=   0.4s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=300, subsample=0.7; total time=   0.3s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=1, min_samples_leaf=1, n_estimators=300, subsample=0.9; total 

[CV] END criterion=mse, learning_rate=0.4, loss=deviance, max_depth=6, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.4, loss=deviance, max_depth=6, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.4, loss=deviance, max_depth=6, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.4, loss=deviance, max_depth=6, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.4, loss=deviance, max_depth=6, min_samples_leaf=2, n_estimators=50, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.05, loss=exponential, max_depth=1, min_samples_leaf=2, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END criterion=mse, learning_rate=0.05, loss=exponential, max_depth=1, min_samples_leaf=2, n_estimators=100, subsample=0.9; total time=   0

[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.5s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.6s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.5s
[CV] END criterion=friedman_mse, learning_rate=0.2, loss=exponential, max_depth=6, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=4, min_samples_leaf=1, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=4, min_samples_leaf=1, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.1, loss=deviance, max_depth=4, min_samples_leaf=1, n_e

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=2, min_samples_leaf=1, n_estimators=100, subsample=0.9; total time=   0.1s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=2, min_samples_leaf=1, n_estimators=100, subsample=0.9; total time=   0.0s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=500, subsample=1.0; total time=   1.2s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=500, subsample=1.0; total time=   1.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=500, subsample=1.0; total time=   1.2s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=5, min_samples_leaf=3, n_estimators=500, subsample=1.0; total time=   1.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=5, min_samples_lea

RandomizedSearchCV(cv=5, estimator=GradientBoostingClassifier(random_state=0),
                   n_iter=200,
                   param_distributions={'criterion': ['friedman_mse', 'mse'],
                                        'learning_rate': [0.05, 0.1, 0.2, 0.3,
                                                          0.4],
                                        'loss': ['deviance', 'exponential'],
                                        'max_depth': [1, 2, 3, 4, 5, 6],
                                        'min_samples_leaf': [1, 2, 3],
                                        'n_estimators': [50, 100, 200, 300, 400,
                                                         500],
                                        'subsample': [0.6, 0.7, 0.8, 0.9, 1.0]},
                   random_state=0, scoring='f1', verbose=2)

In [106]:
resultados_gb_random = best_model_metrics(rgs_cv_gb, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_gb_random_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7132086643833632
F1 score en test set: 0.6666666666666666
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'subsample': 0.8, 'n_estimators': 400, 'min_samples_leaf': 3, 'max_depth': 2, 'loss': 'exponential', 'learning_rate': 0.1, 'criterion': 'mse'}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.97      0.87        96
           1       0.90      0.53      0.67        53

    accuracy                           0.81       149
   macro avg       0.85      0.75      0.77       149
weighted avg       0.83      0.81      0.80       149


 Matriz de Confucion:
[[93  3]
 [25 28]]

 Resultados de los mejores 10 modelos:
    param_subsample param_n_estimators param_min_samples_leaf param_max_depth  \
9               0.9                400                      2               2   
18              0.7                300                      3         

In [44]:
# Mejor del random gridsearch
gb1 = GradientBoostingClassifier(random_state=0, subsample=0.8, n_estimators=400, max_depth=2, learning_rate=0.1, 
                                min_samples_leaf=3, loss='exponential', criterion='mse')

score_train_test(gb1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7132086643833632
F1 score test: 0.6666666666666666


In [108]:
param_grid_gb = {
    'max_depth': [2, 3],
    'n_estimators': [200, 300, 400],
    'learning_rate': [0.05, 0.1, 0.2],
    'subsample': [0.6, 0.7, 0.8, 0.9],
    'criterion': ['friedman_mse', 'mse'],
    'min_samples_leaf': [1, 2, 3, 4],
    'loss': ['deviance', 'exponential']
}

In [109]:
model =  GradientBoostingClassifier(random_state=0)

gs_cv_gb = GridSearchCV(estimator=model, param_grid=param_grid_gb, scoring='f1', cv=5, verbose=2)
gs_cv_gb.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 1152 candidates, totalling 5760 fits
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.6; total time=   0.1s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=200, subsample=0.7; total time=   0.2s
[CV] END criterio

[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.8; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, m

[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.7; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.7; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.8; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.8; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.8; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=2, n_estimators=400, subsample=0.8; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, m

[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.6; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=3, n_estimators=400, subsample=0.7; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, m

[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=300, subsample=0.9; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=300, subsample=0.9; total time=   0.3s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=300, subsample=0.9; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=400, subsample=0.6; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, min_samples_leaf=4, n_estimators=400, subsample=0.6; total time=   0.4s
[CV] END criterion=friedman_mse, learning_rate=0.05, loss=deviance, max_depth=2, m

...

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=1, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=200, subsample=0.6; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=200, subsample=0.6; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=200, subsample=0.6; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=200, subsample=0.6; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=200, subsample=0.

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=400, subsample=0.9; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=2, n_estimators=400, subsample=0.9; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=200, subsample=0.6; total time=   0.2s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=200, subsample=0.

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.8; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.8; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.8; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.9; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.9; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.9; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=3, n_estimators=400, subsample=0.

[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.7; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.8; total time=   0.5s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.8; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.8; total time=   0.6s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.8; total time=   0.7s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.8; total time=   0.7s
[CV] END criterion=mse, learning_rate=0.2, loss=exponential, max_depth=3, min_samples_leaf=4, n_estimators=400, subsample=0.

GridSearchCV(cv=5, estimator=GradientBoostingClassifier(random_state=0),
             param_grid={'criterion': ['friedman_mse', 'mse'],
                         'learning_rate': [0.05, 0.1, 0.2],
                         'loss': ['deviance', 'exponential'],
                         'max_depth': [2, 3], 'min_samples_leaf': [1, 2, 3, 4],
                         'n_estimators': [200, 300, 400],
                         'subsample': [0.6, 0.7, 0.8, 0.9]},
             scoring='f1', verbose=2)

In [110]:
resultados_gb = best_model_metrics(gs_cv_gb, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_gb2_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7136554317400691
F1 score en test set: 0.6823529411764705
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'criterion': 'friedman_mse', 'learning_rate': 0.1, 'loss': 'exponential', 'max_depth': 2, 'min_samples_leaf': 1, 'n_estimators': 400, 'subsample': 0.8}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.97      0.87        96
           1       0.91      0.55      0.68        53

    accuracy                           0.82       149
   macro avg       0.85      0.76      0.78       149
weighted avg       0.83      0.82      0.81       149


 Matriz de Confucion:
[[93  3]
 [24 29]]

 Resultados de los mejores 10 modelos:
    param_criterion param_learning_rate   param_loss param_max_depth  \
172    friedman_mse                0.05  exponential               3   
202    friedman_mse                 0.1     deviance               2   
294    

In [45]:
# Mejor del gridsearch
gb2 = GradientBoostingClassifier(random_state=0, subsample=0.8, n_estimators=400, max_depth=2, learning_rate=0.1, 
                                min_samples_leaf=1, loss='exponential', criterion='friedman_mse')

score_train_test(gb2, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7136554317400691
F1 score test: 0.6823529411764705


### Ensemble

Toma los mejores modelos de cada tipo y los combina aprendiendo a cual darle mas importancia

In [53]:
def ensemble_fit(models, X, y): # X para entrenar
    for model in models:
        model.fit(X, y)
    m = np.zeros((len(X), len(models)))
    for i, model in enumerate(models):
        pred = model.predict(X)
        m[:,i] = pred
    logreg = LogisticRegression()
    logreg.fit(m, y)
    return logreg

def ensemble_predict(models, X, logreg): #X_test
    m = np.zeros((len(X), len(models)))
    for i, model in enumerate(models):
        pred = model.predict(X)
        m[:,i] = pred
    return logreg.predict(m)

def generar_submission_ensemble(models, X_train, y_train, X_submission, test_df, name='submission_ensemble.csv'):
    logreg = ensemble_fit(models, X_train, y_train)
    test_id = test_df["Customer"]
    test_pred = ensemble_predict(models, X_submission, logreg)
    submission = pd.DataFrame(list(zip(test_id, test_pred)), columns=["Customer", "TravelInsurance"])
    submission.to_csv(name, header=True, index=False)
    return len(submission)

In [79]:
models = [svm1, xgb4]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7283653846153846
F1 score en test set: 0.7191011235955056
[[92  4]
 [21 32]]


In [68]:
# Kaggle 0.79545
generar_submission_ensemble(models, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_reentrenado.csv')

497

In [80]:
models = [svm1, xgb4, lr1]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7330873308733088
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]


In [68]:
# Kaggle 0.79545
generar_submission_ensemble(models, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_svm1_xgb4_lr1.csv')

497

In [81]:
models = [svm1, xgb4, lr1, knn2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7343941248470012
F1 score en test set: 0.7209302325581395
[[94  2]
 [22 31]]


In [97]:
# Kaggle 0.78651
generar_submission_ensemble(models, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_svm1_xgb4_lr1_knn2.csv')

497

In [82]:
models = [svm1, xgb4, knn2, rf1, gb2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7372262773722629
F1 score en test set: 0.7209302325581395
[[94  2]
 [22 31]]


In [70]:
# Kaggle  0.79545
generar_submission_ensemble(models, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_svm1_xgb4_knn2_rf1_gb2.csv')

497

In [83]:
models = [svm1, xgb4, rf1, gb2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7320099255583127
F1 score en test set: 0.6976744186046512
[[93  3]
 [23 30]]


In [84]:
models = [svm1, xgb4, knn2, gb2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7376058041112454
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]


In [72]:
# Kaggle 0.78651
generar_submission_ensemble(models, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_svm1_xgb4_knn2_gb2.csv')

497

In [85]:
models = [svm1, xgb4, gb2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7329192546583851
F1 score en test set: 0.6823529411764705
[[93  3]
 [24 29]]


In [55]:
models_1 = [knn1, ada_1]
lr_1 = ensemble_fit(models_1, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models_1, X_scaled, lr_1)
y_pred_test_ensemble = ensemble_predict(models_1, X_test_scaled, lr_1)
print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7380410022779043
F1 score en test set: 0.6736842105263159
[[86 10]
 [21 32]]


In [90]:
# Kaggle 0.72340
generar_submission_ensemble(models_1, X_kaggle_scaled, lr_1, test_df, name='submission_knn_ada.csv')

497

In [63]:
models_1 = [svm1, xgb4, ada_1]
lr_1 = ensemble_fit(models_1, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models_1, X_scaled, lr_1)
y_pred_test_ensemble = ensemble_predict(models_1, X_test_scaled, lr_1)
print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7324290998766955
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]


In [64]:
# Kaggle 0.79545
generar_submission_ensemble(models_1, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_ensemble_svm1_xgb4_ada.csv')

497

In [57]:
models_1 = [ada_1, xgb4]
lr_1 = ensemble_fit(models_1, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models_1, X_scaled, lr_1)
y_pred_test_ensemble = ensemble_predict(models_1, X_test_scaled, lr_1)
print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7317676143386898
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]


### Voting

In [57]:
np.random.seed(3)
w = []
for i in range(40):
    w.append(np.random.rand(1,4).round(1)[0])

In [60]:
param_grid_voting = {
    'voting': ['hard', 'soft'],
    'weights': [None] + w
}

In [61]:
from sklearn.ensemble import VotingClassifier
voting = VotingClassifier([('svm', svm1), ('xgb', xgb4), ('gb', gb2), ('knn', knn2)])

gs_cv_voting = GridSearchCV(voting, param_grid_voting, scoring='f1', cv=5, verbose=2)
gs_cv_voting.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 82 candidates, totalling 410 fits
[CV] END ..........................voting=hard, weights=None; total time=   0.8s
[CV] END ..........................voting=hard, weights=None; total time=   0.9s
[CV] END ..........................voting=hard, weights=None; total time=   0.9s
[CV] END ..........................voting=hard, weights=None; total time=   1.0s
[CV] END ..........................voting=hard, weights=None; total time=   0.9s
[CV] END .............voting=hard, weights=[0.6 0.7 0.3 0.5]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.6 0.7 0.3 0.5]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.6 0.7 0.3 0.5]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.6 0.7 0.3 0.5]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.6 0.7 0.3 0.5]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.9 0.9 0.1 0.2]; total time=   0.8s
[CV] END .............voting=hard, weights=[0.9

[CV] END .............voting=hard, weights=[0.1 0.2 0.2 0.1]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.2 0.2 0.1]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.2 0.2 0.1]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.2 0.2 0.1]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.6 0.2 1. ]; total time=   0.8s
[CV] END .............voting=hard, weights=[0.1 0.6 0.2 1. ]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.6 0.2 1. ]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.6 0.2 1. ]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.1 0.6 0.2 1. ]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.7 0.5 0.7 0.3]; total time=   0.8s
[CV] END .............voting=hard, weights=[0.7 0.5 0.7 0.3]; total time=   0.9s
[CV] END .............voting=hard, weights=[0.7 0.5 0.7 0.3]; total time=   0.9s
[CV] END .............voting

[CV] END .............voting=hard, weights=[1.  0.4 0.2 0.2]; total time=   0.9s
[CV] END .............voting=hard, weights=[1.  0.4 0.2 0.2]; total time=   0.9s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END ..........................voting=soft, weights=None; total time=   0.8s


...

c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END .............voting=soft, weights=[1.  0.4 0.2 0.2]; total time=   0.8s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END .............voting=soft, weights=[1.  0.4 0.2 0.2]; total time=   0.8s


GridSearchCV(cv=5,
             estimator=VotingClassifier(estimators=[('svm',
                                                     SVC(C=100, gamma=0.0316)),
                                                    ('xgb',
                                                     XGBClassifier(base_score=0.5,
                                                                   booster='gbtree',
                                                                   colsample_bylevel=1,
                                                                   colsample_bynode=1,
                                                                   colsample_bytree=0.7,
                                                                   eval_metric='logloss',
                                                                   gamma=1,
                                                                   gpu_id=-1,
                                                                   importance_type='gain',
              

In [62]:
resultados_voting = best_model_metrics(gs_cv_voting, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_voting1_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7110694145533989
F1 score en test set: 0.6823529411764705
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'voting': 'hard', 'weights': array([0.9, 0.8, 0.4, 0.1])}

 Classification Report:
              precision    recall  f1-score   support

           0       0.79      0.97      0.87        96
           1       0.91      0.55      0.68        53

    accuracy                           0.82       149
   macro avg       0.85      0.76      0.78       149
weighted avg       0.83      0.82      0.81       149


 Matriz de Confucion:
[[93  3]
 [24 29]]

 Resultados de los mejores 10 modelos:
   param_voting         param_weights  \
9          hard  [0.9, 0.8, 0.4, 0.1]   
10         hard  [0.7, 0.6, 0.4, 0.2]   
19         hard  [0.7, 0.5, 0.6, 0.1]   
22         hard  [0.7, 0.5, 0.7, 0.3]   
23         hard  [0.9, 0.8, 0.7, 0.5]   
25         hard  [0.6, 0.4, 0.6, 0.2]   
28         hard  [0.9, 0.8, 0.

In [87]:
# Mejor del gridsearch
voting1 = VotingClassifier([('svm', svm1), ('xgb', xgb4), ('gb', gb2), ('knn', knn2)], voting='hard', weights=np.array([0.9, 0.8, 0.4, 0.1]))

score_train_test(voting1, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7110694145533989
F1 score test: 0.6823529411764705


In [75]:
np.random.seed(3)
w2 = []
for i in range(20):
    w2.append(np.random.rand(1,2).round(1)[0])

In [76]:
param_grid_voting2 = {
    'voting': ['hard', 'soft'],
    'weights': [None] + w2
}

In [77]:
from sklearn.ensemble import VotingClassifier
voting2 = VotingClassifier([('svm', svm1), ('xgb', xgb4)])

gs_cv_voting2 = GridSearchCV(voting2, param_grid_voting2, scoring='f1', cv=5, verbose=2)
gs_cv_voting2.fit(X_scaled, y_scaled)

Fitting 5 folds for each of 42 candidates, totalling 210 fits
[CV] END ..........................voting=hard, weights=None; total time=   0.4s
[CV] END ..........................voting=hard, weights=None; total time=   0.5s
[CV] END ..........................voting=hard, weights=None; total time=   0.4s
[CV] END ..........................voting=hard, weights=None; total time=   0.4s
[CV] END ..........................voting=hard, weights=None; total time=   0.5s
[CV] END .....................voting=hard, weights=[0.6 0.7]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.6 0.7]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.6 0.7]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.6 0.7]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.6 0.7]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.3 0.5]; total time=   0.4s
[CV] END .....................voting=hard, weig

[CV] END .....................voting=hard, weights=[0.4 0.2]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.4 0.2]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.4 0.2]; total time=   0.4s
[CV] END .....................voting=hard, weights=[0.4 0.2]; total time=   0.5s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END ..........................voting=soft, weights=None; total time=   0.4s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

...

c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END .....................voting=soft, weights=[0.4 0.2]; total time=   0.4s


c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py:696: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\model_selection\_validation.py", line 687, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 199, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true,
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 236, in _score
    y_pred = method_caller(estimator, "predict", X)
  File "c:\users\sofia\appdata\local\programs\python\python39\lib\site-packages\sklearn\metrics\_scorer.py", line 53, in _cached_call
    return getattr(est

[CV] END .....................voting=soft, weights=[0.4 0.2]; total time=   0.4s


GridSearchCV(cv=5,
             estimator=VotingClassifier(estimators=[('svm',
                                                     SVC(C=100, gamma=0.0316)),
                                                    ('xgb',
                                                     XGBClassifier(base_score=0.5,
                                                                   booster='gbtree',
                                                                   colsample_bylevel=1,
                                                                   colsample_bynode=1,
                                                                   colsample_bytree=0.7,
                                                                   eval_metric='logloss',
                                                                   gamma=1,
                                                                   gpu_id=-1,
                                                                   importance_type='gain',
              

In [78]:
resultados_voting2 = best_model_metrics(gs_cv_voting2, X_test_scaled, y_test_scaled, results=True, save=True, name='resultados_voting2_encoding1.csv', ret=True)

F1 score promedio del modelo en train set: 0.7097027987071336
F1 score en test set: 0.7126436781609194
OJO: Si en el train set da mucho mayor, probablemente este overfitteando

 Parametros:
{'voting': 'hard', 'weights': array([0.6, 0.7])}

 Classification Report:
              precision    recall  f1-score   support

           0       0.81      0.97      0.88        96
           1       0.91      0.58      0.71        53

    accuracy                           0.83       149
   macro avg       0.86      0.78      0.80       149
weighted avg       0.85      0.83      0.82       149


 Matriz de Confucion:
[[93  3]
 [22 31]]

 Resultados de los mejores 10 modelos:
   param_voting param_weights                                     params  \
1          hard    [0.6, 0.7]  {'voting': 'hard', 'weights': [0.6, 0.7]}   
2          hard    [0.3, 0.5]  {'voting': 'hard', 'weights': [0.3, 0.5]}   
4          hard    [0.1, 0.2]  {'voting': 'hard', 'weights': [0.1, 0.2]}   
5          hard    [0.1

In [88]:
# Mejor del gridsearch
voting2 = VotingClassifier([('svm', svm1), ('xgb', xgb4)], voting='hard', weights=np.array([0.6, 0.7]))

score_train_test(voting2, X_scaled, y_scaled, X_test_scaled, y_test_scaled)

F1 score cross-validation: 0.7097027987071336
F1 score test: 0.7126436781609194


In [89]:
generar_submission(voting2, X_train_scaled, y_train_scaled, X_kaggle_scaled, test_df, name='submission_voting2.csv')

497

## Mejores modelos

Los modelos que obtuvieron los mejores scores en el conjunto de train y en el de kaggle son los siguientes ensembles:

In [71]:
models = [svm1, xgb4, lr1]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7330873308733088
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]


In [74]:
models = [svm1, xgb4, knn2, rf1, gb2]
lr = ensemble_fit(models, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models, X_scaled, lr)
y_pred_test_ensemble = ensemble_predict(models, X_test_scaled, lr)

print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7372262773722629
F1 score en test set: 0.7209302325581395
[[94  2]
 [22 31]]


In [73]:
models_1 = [svm1, xgb4, ada_1]
lr_1 = ensemble_fit(models_1, X_scaled, y_scaled)
y_pred_train_ensemble = ensemble_predict(models_1, X_scaled, lr_1)
y_pred_test_ensemble = ensemble_predict(models_1, X_test_scaled, lr_1)
print('F1 score en train set:', f1_score(y_scaled, y_pred_train_ensemble))
print('F1 score en test set:', f1_score(y_test_scaled, y_pred_test_ensemble))
print(confusion_matrix(y_test_scaled, y_pred_test_ensemble))

F1 score en train set: 0.7324290998766955
F1 score en test set: 0.7126436781609194
[[93  3]
 [22 31]]
